### 2018/2019 - Task List 10

1. Implement Naive Bayes classifier with pyro
    - create apropriate parameters (mean and std for a and b, sigma - noise)
    - provide optimization procedure
    - check appropriateness of implemented method with selected dataset


# Required imports

In [69]:
%matplotlib inline
import pyro
import torch
import numpy as np
import matplotlib.pyplot as plt
import pyro.optim as optim
import pyro.distributions as dist
from torch.distributions import constraints
from tqdm import tqdm
import seaborn as sns
from matplotlib import animation, rc
from IPython.display import HTML
import torch.nn as nn
from functools import partial
import pandas as pd
from pyro.contrib.autoguide import AutoDiagonalNormal
from pyro.infer import EmpiricalMarginal, SVI, Trace_ELBO, TracePredictive
from sklearn.base import BaseEstimator
import scipy.stats

In [2]:
pyro.set_rng_seed(1)
pyro.enable_validation(True)

In [3]:
from sklearn import datasets, model_selection
from sklearn.naive_bayes import GaussianNB


## Solutions

### sklearn solution

In [4]:
torch.set_default_tensor_type(torch.DoubleTensor)

In [5]:
iris = datasets.load_iris()

gnb = GaussianNB()


X_train, X_validation, Y_train, Y_validation = model_selection.train_test_split(
    iris.data, iris.target, test_size=0.33, random_state=5)

In [7]:
kfold = 5
scoring = ['accuracy', 'f1_micro', 'f1_macro']
cv_results = model_selection.cross_validate(gnb, X_train, Y_train, cv=kfold, scoring=scoring)

#displaying the mean and standard deviation of the prediction
for score in scoring: 
    msg = "%s: %f (%f)" % ('NB ' + score, cv_results['test_' + score].mean(), cv_results['test_' + score].std())
    print(msg)

NB accuracy: 0.960902 (0.035958)
NB f1_micro: 0.960902 (0.035958)
NB f1_macro: 0.960191 (0.036241)


### self-made NB

In [155]:
class NaiveBayesClassifier(BaseEstimator):
    
    def __init__(self):
        pass
    
    def fit(self, x_data, y_data):
        self.x = x_data
        self.y = y_data
        self.attributes_number = x_data.shape[1]
        self.classes = np.unique(y_data)
        
        self.cat_probs = self.y_train(self.y)
        
        div_data = self.div_by_category_and_attribute(self.x, self.y)
        self.params = {}
        for key in div_data.keys():
            mean, scale, losses = self.train(div_data[key], key)
            self.params[key] = {"mean":mean, "scale":scale}
        
    
    def predict(self, data):
        predictions = list()

        for x in data:
            max_prob = -1
            prediction = None
            for category in self.classes:
                prob = 1
                for attr in range(self.attributes_number):
                    mean = self.params[(category, attr)]['mean'].item()
                    scale = self.params[(category, attr)]['scale'].item()
                    prob = prob * scipy.stats.norm(mean, scale).pdf(x[attr])
                prob = prob * self.cat_probs[category].item()
                
                if prob > max_prob:
                    max_prob = prob
                    prediction = category
            predictions.append(prediction)
        return predictions
    
    def div_by_category_and_attribute(self, x_data, y_data):
        X_cl = {}

        for i in range(len(x_data)):
            for attribute in range(len(x_data[0])):
                if (y_data[i], attribute) not in X_cl.keys():
                    X_cl[(y_data[i], attribute)] = list()
                X_cl[(y_data[i], attribute)].append(x_data[i][attribute])

        for cl_key in np.unique(y_data):
            for attribute in range(len(x_data[0])):
                X_cl[cl_key, attribute] = np.array(X_cl[cl_key, attribute])

        return X_cl
    
    def model(self, x_data, label):
        mean = pyro.param('mean' + str(label),  x_data.mean())
        scale = pyro.param('scale' + str(label), torch.tensor(1.0).double(), constraint=constraints.positive)
        with pyro.plate('data_loop' + str(label), len(x_data)):
            pyro.sample('prob' + str(label), dist.Normal(mean, scale), obs=x_data)
       
    def guide(self, x_data, label):
        mean = pyro.param('mean' + str(label), torch.tensor(2.0))
        scale = pyro.param('scale' + str(label), torch.tensor(1.0), constraint=constraints.positive)
        pyro.sample('prob' + str(label), dist.Normal(mean.double(), scale.double()), infer={'is_auxiliary': True})
    
    def y_model(self, data):
        # we sample three values from Beta distribution with alfa=6 and beta=10 that distributions peaks around 0.33 for every class
        # samples do not sum up to 1, we make them independent
        alpha = torch.tensor(6.0)
        beta = torch.tensor(10.0)
        cat_probs = pyro.sample('cat_probs', dist.Beta(alpha, beta).expand([3]).independent(1))
        normalized_cat_probs = cat_probs / torch.sum(cat_probs)

        with pyro.iarange('cat_data_loop', len(data)):
            pyro.sample('obs', dist.Categorical(probs=normalized_cat_probs), obs=data)
    
    def y_guide(self, data):
        alphas = pyro.param('alphas', torch.tensor(6.).expand(3), constraint=constraints.positive)
        betas = pyro.param('betas', torch.tensor(10.).expand(3), constraint=constraints.positive) 

        pyro.sample('cat_probs', dist.Beta(alphas, betas).independent(1))
    
    def y_train(self, y_data):
        adam_params = {"lr": 0.0005}
        optimizer = pyro.optim.Adam(adam_params)
        svi = SVI(y_model, y_guide, optimizer, loss=Trace_ELBO())

        n_steps = 2501
        for step in range(n_steps):
            svi.step(torch.from_numpy(Y_train))
            
        alphas = pyro.param("alphas")
        betas = pyro.param("betas")

        means = alphas / (alphas + betas)
        normalized_means = means / torch.sum(means)
#         factors = betas / (alphas * (1.0 + alphas + betas))
#         stdevs = normalized_means * torch.sqrt(factors)
        return normalized_means
    
    def train(self, data, label, num_steps=1000):
        pyro.clear_param_store()

        optim = pyro.optim.Adam({"lr": 0.045})
        svi = pyro.infer.SVI(model=self.model,
                             guide=self.guide,
                             optim=optim,
                             loss=pyro.infer.Trace_ELBO(),
                             num_samples=len(data))

        losses = []
        print("Learning for class: " + str(label[0]) + " and attribute: " + str(label[1]))
        t = tqdm(range(num_steps))
        for j in t:
            loss = svi.step(torch.from_numpy(data), label)
            losses.append(loss)
            t.set_postfix(loss=loss)
        return pyro.param("mean" + str(label)), pyro.param("scale" + str(label)), losses

    

In [156]:
nbc = NaiveBayesClassifier()

In [157]:
kfold = 5
scoring = ['accuracy', 'f1_micro', 'f1_macro']
cv_results = model_selection.cross_validate(nbc, X_train, Y_train, cv=kfold, scoring=scoring)






  0%|          | 0/1000 [00:00<?, ?it/s]



  0%|          | 0/1000 [00:00<?, ?it/s, loss=325]



  0%|          | 0/1000 [00:00<?, ?it/s, loss=294]



  0%|          | 0/1000 [00:00<?, ?it/s, loss=265]



  0%|          | 0/1000 [00:00<?, ?it/s, loss=246]



  0%|          | 0/1000 [00:00<?, ?it/s, loss=223]



  0%|          | 0/1000 [00:00<?, ?it/s, loss=205]



  0%|          | 0/1000 [00:00<?, ?it/s, loss=187]



  0%|          | 0/1000 [00:00<?, ?it/s, loss=175]



  0%|          | 0/1000 [00:00<?, ?it/s, loss=163]



  0%|          | 0/1000 [00:00<?, ?it/s, loss=151]



  0%|          | 0/1000 [00:00<?, ?it/s, loss=142]



  0%|          | 0/1000 [00:00<?, ?it/s, loss=134]



  1%|          | 12/1000 [00:00<00:09, 108.18it/s, loss=134]



  1%|          | 12/1000 [00:00<00:09, 108.18it/s, loss=126]



  1%|          | 12/1000 [00:00<00:09, 108.18it/s, loss=117]



  1%|          | 12/1000 [00:00<00:09, 108.18it/s, loss=114]



  1%|          | 12/1000 [00:00<00:09, 108.18it/

Learning for class: 2 and attribute: 0






  1%|          | 12/1000 [00:00<00:09, 108.18it/s, loss=86.9]



  1%|          | 12/1000 [00:00<00:09, 108.18it/s, loss=85.4]



  2%|▏         | 24/1000 [00:00<00:08, 108.83it/s, loss=85.4]



  2%|▏         | 24/1000 [00:00<00:08, 108.83it/s, loss=84]  



  2%|▏         | 24/1000 [00:00<00:08, 108.83it/s, loss=81.6]



  2%|▏         | 24/1000 [00:00<00:08, 108.83it/s, loss=81.4]



  2%|▏         | 24/1000 [00:00<00:08, 108.83it/s, loss=79.7]



  2%|▏         | 24/1000 [00:00<00:08, 108.83it/s, loss=79.1]



  2%|▏         | 24/1000 [00:00<00:08, 108.83it/s, loss=78.1]



  2%|▏         | 24/1000 [00:00<00:08, 108.83it/s, loss=77.3]



  2%|▏         | 24/1000 [00:00<00:08, 108.83it/s, loss=77]  



  2%|▏         | 24/1000 [00:00<00:08, 108.83it/s, loss=76]



  2%|▏         | 24/1000 [00:00<00:08, 108.83it/s, loss=75.7]



  2%|▏         | 24/1000 [00:00<00:08, 108.83it/s, loss=75.4]



  2%|▏         | 24/1000 [00:00<00:08, 108.83it/s, loss=75]  



  4%|▎         | 36/100

 11%|█▏        | 113/1000 [00:01<00:07, 113.76it/s, loss=64.6]



 11%|█▏        | 113/1000 [00:01<00:07, 113.76it/s, loss=64.1]



 11%|█▏        | 113/1000 [00:01<00:07, 113.76it/s, loss=64.6]



 11%|█▏        | 113/1000 [00:01<00:07, 113.76it/s, loss=63.8]



 11%|█▏        | 113/1000 [00:01<00:07, 113.76it/s, loss=63.8]



 12%|█▎        | 125/1000 [00:01<00:07, 114.17it/s, loss=63.8]



 12%|█▎        | 125/1000 [00:01<00:07, 114.17it/s, loss=64.3]



 12%|█▎        | 125/1000 [00:01<00:07, 114.17it/s, loss=64.1]



 12%|█▎        | 125/1000 [00:01<00:07, 114.17it/s, loss=59.1]



 12%|█▎        | 125/1000 [00:01<00:07, 114.17it/s, loss=63.8]



 12%|█▎        | 125/1000 [00:01<00:07, 114.17it/s, loss=63.8]



 12%|█▎        | 125/1000 [00:01<00:07, 114.17it/s, loss=62.8]



 12%|█▎        | 125/1000 [00:01<00:07, 114.17it/s, loss=63.6]



 12%|█▎        | 125/1000 [00:01<00:07, 114.17it/s, loss=63.5]



 12%|█▎        | 125/1000 [00:01<00:07, 114.17it/s, loss=63.2]



 12%|█▎   

 22%|██▏       | 216/1000 [00:01<00:06, 127.33it/s, loss=48.1]



 22%|██▏       | 216/1000 [00:01<00:06, 127.33it/s, loss=48]  



 22%|██▏       | 216/1000 [00:01<00:06, 127.33it/s, loss=47.4]



 22%|██▏       | 216/1000 [00:01<00:06, 127.33it/s, loss=47.2]



 22%|██▏       | 216/1000 [00:01<00:06, 127.33it/s, loss=45.3]



 22%|██▏       | 216/1000 [00:01<00:06, 127.33it/s, loss=46.9]



 22%|██▏       | 216/1000 [00:01<00:06, 127.33it/s, loss=46.6]



 22%|██▏       | 216/1000 [00:01<00:06, 127.33it/s, loss=45.9]



 22%|██▏       | 216/1000 [00:01<00:06, 127.33it/s, loss=45.6]



 22%|██▏       | 216/1000 [00:01<00:06, 127.33it/s, loss=45.7]



 22%|██▏       | 216/1000 [00:01<00:06, 127.33it/s, loss=45.5]



 23%|██▎       | 229/1000 [00:01<00:07, 107.79it/s, loss=45.5]



 23%|██▎       | 229/1000 [00:01<00:07, 107.79it/s, loss=44.8]



 23%|██▎       | 229/1000 [00:01<00:07, 107.79it/s, loss=44.9]



 23%|██▎       | 229/1000 [00:01<00:07, 107.79it/s, loss=44.8]



 23%|██▎  

...

 70%|███████   | 704/1000 [00:04<00:01, 149.24it/s, loss=-4.67]



 70%|███████   | 704/1000 [00:04<00:01, 149.24it/s, loss=-4.41]



 70%|███████   | 704/1000 [00:04<00:01, 149.24it/s, loss=-4.52]



 70%|███████   | 704/1000 [00:04<00:01, 149.24it/s, loss=-5.96]



 70%|███████   | 704/1000 [00:04<00:01, 149.24it/s, loss=-4.4] 



 70%|███████   | 704/1000 [00:04<00:01, 149.24it/s, loss=-4.53]



 70%|███████   | 704/1000 [00:04<00:01, 149.24it/s, loss=-4.4] 



 70%|███████   | 704/1000 [00:04<00:01, 149.24it/s, loss=-4.64]



 70%|███████   | 704/1000 [00:04<00:01, 149.24it/s, loss=-4.8] 



 70%|███████   | 704/1000 [00:04<00:01, 149.24it/s, loss=-5.16]



 70%|███████   | 704/1000 [00:04<00:01, 149.24it/s, loss=-4.42]



 70%|███████   | 704/1000 [00:04<00:01, 149.24it/s, loss=-4.42]



 70%|███████   | 704/1000 [00:04<00:01, 149.24it/s, loss=-4.42]



 70%|███████   | 704/1000 [00:04<00:01, 149.24it/s, loss=-4.41]



 70%|███████   | 704/1000 [00:04<00:01, 149.24it/s, loss=-4.71

 80%|███████▉  | 796/1000 [00:05<00:01, 145.30it/s, loss=-4.6] 



 80%|███████▉  | 796/1000 [00:05<00:01, 145.30it/s, loss=-4.4]



 80%|███████▉  | 796/1000 [00:05<00:01, 145.30it/s, loss=-4.58]



 80%|███████▉  | 796/1000 [00:05<00:01, 145.30it/s, loss=-4.42]



 80%|███████▉  | 796/1000 [00:05<00:01, 145.30it/s, loss=-4.44]



 80%|███████▉  | 796/1000 [00:05<00:01, 145.30it/s, loss=-4.8] 



 80%|███████▉  | 796/1000 [00:05<00:01, 145.30it/s, loss=-4.42]



 80%|███████▉  | 796/1000 [00:05<00:01, 145.30it/s, loss=-4.95]



 80%|███████▉  | 796/1000 [00:05<00:01, 145.30it/s, loss=-4.4] 



 80%|███████▉  | 796/1000 [00:05<00:01, 145.30it/s, loss=-5.02]



 80%|███████▉  | 796/1000 [00:05<00:01, 145.30it/s, loss=-4.4] 



 80%|███████▉  | 796/1000 [00:05<00:01, 145.30it/s, loss=-5.45]



 80%|███████▉  | 796/1000 [00:05<00:01, 145.30it/s, loss=-6.06]



 81%|████████▏ | 813/1000 [00:05<00:01, 151.21it/s, loss=-6.06]



 81%|████████▏ | 813/1000 [00:05<00:01, 151.21it/s, loss=-7.46]

 90%|████████▉ | 898/1000 [00:06<00:00, 148.65it/s, loss=-7.11]



 90%|████████▉ | 898/1000 [00:06<00:00, 148.65it/s, loss=-5.57]



 90%|████████▉ | 898/1000 [00:06<00:00, 148.65it/s, loss=-4.83]



 90%|████████▉ | 898/1000 [00:06<00:00, 148.65it/s, loss=-6.47]



 90%|████████▉ | 898/1000 [00:06<00:00, 148.65it/s, loss=-4.74]



 90%|████████▉ | 898/1000 [00:06<00:00, 148.65it/s, loss=-5.04]



 90%|████████▉ | 898/1000 [00:06<00:00, 148.65it/s, loss=-4.49]



 90%|████████▉ | 898/1000 [00:06<00:00, 148.65it/s, loss=-4.58]



 90%|████████▉ | 898/1000 [00:06<00:00, 148.65it/s, loss=-4.41]



 90%|████████▉ | 898/1000 [00:06<00:00, 148.65it/s, loss=-4.48]



 90%|████████▉ | 898/1000 [00:06<00:00, 148.65it/s, loss=-4.91]



 90%|████████▉ | 898/1000 [00:06<00:00, 148.65it/s, loss=-4.75]



 90%|████████▉ | 898/1000 [00:06<00:00, 148.65it/s, loss=-4.68]



 90%|████████▉ | 898/1000 [00:06<00:00, 148.65it/s, loss=-5.33]



 90%|████████▉ | 898/1000 [00:06<00:00, 148.65it/s, loss=-4.58

 99%|█████████▉| 993/1000 [00:06<00:00, 153.38it/s, loss=-5.04]



 99%|█████████▉| 993/1000 [00:06<00:00, 153.38it/s, loss=-5.29]



 99%|█████████▉| 993/1000 [00:06<00:00, 153.38it/s, loss=-4.41]



 99%|█████████▉| 993/1000 [00:06<00:00, 153.38it/s, loss=-4.93]



 99%|█████████▉| 993/1000 [00:06<00:00, 153.38it/s, loss=-4.43]



 99%|█████████▉| 993/1000 [00:06<00:00, 153.38it/s, loss=-4.4] 



100%|██████████| 1000/1000 [00:06<00:00, 148.07it/s, loss=-4.4]

NB accuracy: 0.950000 (0.031623)
NB f1_micro: 0.950000 (0.031623)
NB f1_macro: 0.946623 (0.031833)


In [158]:
#displaying the mean and standard deviation of the prediction
for score in scoring: 
    msg = "%s: %f (%f)" % ('NB ' + score, cv_results['test_' + score].mean(), cv_results['test_' + score].std())
    print(msg)

NB accuracy: 0.950000 (0.031623)
NB f1_micro: 0.950000 (0.031623)
NB f1_macro: 0.946623 (0.031833)


In [140]:
alphas = pyro.param("alphas")
betas = pyro.param("betas")

means = alphas / (alphas + betas)
normalized_means = means / torch.sum(means)
factors = betas / (alphas * (1.0 + alphas + betas))
stdevs = normalized_means * torch.sqrt(factors)

In [143]:
normalized_means


tensor([0.3380, 0.3329, 0.3291], grad_fn=<DivBackward0>)

In [144]:
normalized_means[0].item()

0.3379770906053408